# Human Performance Monitoring Module (HPMM version 2)

Authors <br>
&nbsp; - Jiawei Chen, Ruoxin Xiong - Carnegie Mellon University;<br>&nbsp; - Mustafa Demir, Nancy Cooke, Sarah Ligda, Chris  Lieber, Meet Sanghvi, Ashish Amresh - Arizona State University <br>
Email
 &nbsp; <ruoxinx@andrew.cmu.edu>, <mustafa.demir@asu.edu>, <Nancy.Cooke@asu.edu>, <sligda@asu.edu>, <clieber@asu.edu>,<Meet.Sanghvi@asu.edu>, <amresh@asu.edu>;

This module predicts the loss of separation as an indicator of the air traffic controller's operational performance.

Loss of separation is a situation where aircraft fail to maintain minimum distances in controlled airspace.

More information about CatBoost can be found here - https://arxiv.org/abs/1706.09516

This module takes input a list of independent vairables which are selected by the HFM module which calculates the best formula based on a set of input variables

## Code Requirements

- pandas - https://pandas.pydata.org/pandas-docs/stable/getting_started/install.html <br>
- sklearn - https://scikit-learn.org/stable/install.html <br>
- catboost - https://catboost.ai/docs/installation/python-installation-method-pip-install.html

## How to use this file?
- Edit the fields and file name to be used from the csv data file you are passing
- Edit the mapping dictionary = data_type_for_each_column ==> which state which column from the csv file is what type of data

## Preprocessing Note
- The code does processing of the data file provided
- it removes/deletes all rows from the csv where value is NaN

In [1]:
import pandas as pd
from catboost import CatBoostRegressor
from catboost import Pool
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

#### Edit this dictionary to map your column with the data type

In [2]:
data_type_for_each_column = {
    "Ss": "int",
    "condtn": "str",
    "baseline": "int",
    "highworkload": "int",
    "highworkload offnominal": "int",
    "at_sec": "int",
    "traffic_density": "int",
    "los_freq": "int",
    "los_duration_over5min": "int",
    "query": "str",
    "ready_latency": "float",
    "ready_latency_adj": "float",
    "query_latency": "float",
    "response_index": "int",
    "ready_timed_out": "int",
    "query_timed_out": "int",
    "stimuli": "str",
    "response_text": "str",
    "sa_correct": "float",
    "wl_rating": "int",
    "interbeat_interval": "float",
    "condtn_num": "int",
    "face_conf": "str",
    "rx": "float",
    "ry": "float",
    "rz": "float",
    "eyeblink": "float",
    "positive": "float",
    "neutral": "float",
    "negative": "float",
    "emo_conf": "int",
    "los_severity": "float",
    "CLCD": "int",
    "In_transmission (binary)": "int",
    "transmission started (count)": "int",
    "transmission ended (count)": "int",
    "words per transmission (syn_complexity)": "int",
    "length of transmission(in_sec)": "float",
    "Words_sec": "float",
    "time filled in previous interval (up to 5 seconds)": "float",
    "time since last transmissions": "float",
    "True Pilot or ATC": "str",
    "Interval-Pilot (p) OR ATC (a) (ap for shared intervals)": "str",
    "pilot communication time": "float",
    "air traffic communication time in previous interval": "float",
    "ratio of comms at interval P:A": "str",
}

In [3]:
class HPMM(object):
    def __init__(self, cfg):
        self.data = pd.read_csv(cfg['file_name'],
                                usecols=cfg['fields'])

    def preprocessing(self):
        # drop the rows which have NaN elements
        self.data = self.data.dropna()

        # convert each column as the data type it is supposed to be - by default pandas sometimes reads columns as
        # objects instead of strings or ints
        for col in self.data.columns.values:
            self.data[col] = self.data[col].astype(data_type_for_each_column[col])

        return self.data

    # def modelpredict(model, input):
    #     return model.predict(input)
    #
    # def train(self, model, train_pool, test_pool, plot):
    #     model.fit(train_pool, eval_set=test_pool, plot=plot)

## Code Starts Here

#### Edit the fields name & the file_name of the csv data which you are passing

In [6]:
cfg = {
    "fields": ['traffic_density', 'interbeat_interval', 'rz', 'negative', 'positive', 'Words_sec', 'query_latency',
               'sa_correct', 'neutral', 'rx', 'los_freq'],
    # los frequency is the dependent variable here. you can also use los_severity
    # all others are independent variables which are received from the HFM module which calculates the best formula
    'file_name': "data.csv"
}

In [7]:
hpmm = HPMM(cfg)
data = hpmm.preprocessing()

#### Edit these variables

In [8]:
X = data.drop(columns=['los_freq'])
Y = data['los_freq']  # instead of loss frequency use loss of separation severity

In [9]:
scaler = StandardScaler()
X = scaler.fit_transform(X)

### Test-Train Split

In [10]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=10)

### Model Selection

In [12]:
model = CatBoostRegressor()
train_pool = Pool(X_train, y_train)
test_pool = Pool(X_test, y_test)
grid = {'learning_rate': [0.01, 0.05, 0.1],
        'depth': [4, 6, 10],
        'l2_leaf_reg': [1, 3, 5, 7, 9],
        }

In [13]:
grid_search_result = model.grid_search(grid, X=X_train, y=y_train, cv=3, plot=True)
# choose parameters based on grid_search results
model = CatBoostRegressor(
    iterations=1000,
    depth=6,
    learning_rate=0.1,
    l2_leaf_reg=3,
    loss_function='RMSE',  # change loss calculation method
    eval_metric='R2',
    random_seed=1234
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 1.0859556	test: 1.2517270	best: 1.2517270 (0)	total: 177ms	remaining: 2m 57s
1:	learn: 1.0780971	test: 1.2434733	best: 1.2434733 (1)	total: 178ms	remaining: 1m 28s
2:	learn: 1.0705501	test: 1.2354274	best: 1.2354274 (2)	total: 179ms	remaining: 59.5s
3:	learn: 1.0631422	test: 1.2288662	best: 1.2288662 (3)	total: 180ms	remaining: 44.8s
4:	learn: 1.0558919	test: 1.2210645	best: 1.2210645 (4)	total: 180ms	remaining: 35.9s
5:	learn: 1.0486679	test: 1.2134701	best: 1.2134701 (5)	total: 181ms	remaining: 30s
6:	learn: 1.0412512	test: 1.2059494	best: 1.2059494 (6)	total: 182ms	remaining: 25.8s
7:	learn: 1.0342074	test: 1.1985944	best: 1.1985944 (7)	total: 183ms	remaining: 22.7s
8:	learn: 1.0272142	test: 1.1922770	best: 1.1922770 (8)	total: 183ms	remaining: 20.2s
9:	learn: 1.0203028	test: 1.1854043	best: 1.1854043 (9)	total: 184ms	remaining: 18.2s
10:	learn: 1.0135842	test: 1.1784835	best: 1.1784835 (10)	total: 185ms	remaining: 16.6s
11:	learn: 1.0069685	test: 1.1724447	best: 1.1724447

189:	learn: 0.5273620	test: 0.6655038	best: 0.6655038 (189)	total: 313ms	remaining: 1.34s
190:	learn: 0.5266979	test: 0.6647188	best: 0.6647188 (190)	total: 314ms	remaining: 1.33s
191:	learn: 0.5259438	test: 0.6638347	best: 0.6638347 (191)	total: 315ms	remaining: 1.32s
192:	learn: 0.5252813	test: 0.6633207	best: 0.6633207 (192)	total: 316ms	remaining: 1.32s
193:	learn: 0.5246287	test: 0.6624017	best: 0.6624017 (193)	total: 316ms	remaining: 1.31s
194:	learn: 0.5236483	test: 0.6612351	best: 0.6612351 (194)	total: 317ms	remaining: 1.31s
195:	learn: 0.5229675	test: 0.6608413	best: 0.6608413 (195)	total: 318ms	remaining: 1.3s
196:	learn: 0.5221009	test: 0.6597273	best: 0.6597273 (196)	total: 318ms	remaining: 1.3s
197:	learn: 0.5212562	test: 0.6588464	best: 0.6588464 (197)	total: 319ms	remaining: 1.29s
198:	learn: 0.5204648	test: 0.6581820	best: 0.6581820 (198)	total: 320ms	remaining: 1.29s
199:	learn: 0.5196454	test: 0.6567856	best: 0.6567856 (199)	total: 320ms	remaining: 1.28s
200:	learn: 

403:	learn: 0.4514119	test: 0.5851647	best: 0.5851647 (403)	total: 457ms	remaining: 674ms
404:	learn: 0.4512578	test: 0.5850347	best: 0.5850347 (404)	total: 457ms	remaining: 672ms
405:	learn: 0.4510256	test: 0.5846159	best: 0.5846159 (405)	total: 458ms	remaining: 670ms
406:	learn: 0.4508975	test: 0.5846119	best: 0.5846119 (406)	total: 459ms	remaining: 668ms
407:	learn: 0.4507382	test: 0.5845045	best: 0.5845045 (407)	total: 459ms	remaining: 667ms
408:	learn: 0.4505188	test: 0.5840987	best: 0.5840987 (408)	total: 460ms	remaining: 665ms
409:	learn: 0.4504167	test: 0.5842273	best: 0.5840987 (408)	total: 461ms	remaining: 663ms
410:	learn: 0.4501730	test: 0.5841512	best: 0.5840987 (408)	total: 461ms	remaining: 661ms
411:	learn: 0.4501029	test: 0.5841527	best: 0.5840987 (408)	total: 462ms	remaining: 659ms
412:	learn: 0.4499283	test: 0.5838333	best: 0.5838333 (412)	total: 463ms	remaining: 657ms
413:	learn: 0.4497708	test: 0.5836868	best: 0.5836868 (413)	total: 463ms	remaining: 656ms
414:	learn

605:	learn: 0.4230064	test: 0.5654126	best: 0.5653577 (604)	total: 602ms	remaining: 391ms
606:	learn: 0.4229340	test: 0.5653599	best: 0.5653577 (604)	total: 603ms	remaining: 390ms
607:	learn: 0.4228249	test: 0.5652869	best: 0.5652869 (607)	total: 604ms	remaining: 389ms
608:	learn: 0.4226881	test: 0.5652152	best: 0.5652152 (608)	total: 604ms	remaining: 388ms
609:	learn: 0.4226096	test: 0.5653195	best: 0.5652152 (608)	total: 605ms	remaining: 387ms
610:	learn: 0.4224298	test: 0.5649918	best: 0.5649918 (610)	total: 606ms	remaining: 386ms
611:	learn: 0.4221727	test: 0.5649025	best: 0.5649025 (611)	total: 606ms	remaining: 384ms
612:	learn: 0.4220152	test: 0.5647587	best: 0.5647587 (612)	total: 607ms	remaining: 383ms
613:	learn: 0.4218876	test: 0.5646487	best: 0.5646487 (613)	total: 608ms	remaining: 382ms
614:	learn: 0.4216796	test: 0.5646229	best: 0.5646229 (614)	total: 608ms	remaining: 381ms
615:	learn: 0.4215061	test: 0.5643120	best: 0.5643120 (615)	total: 609ms	remaining: 380ms
616:	learn

...

887:	learn: 0.0207263	test: 0.5737825	best: 0.5733151 (550)	total: 22.2s	remaining: 2.8s
888:	learn: 0.0207078	test: 0.5737748	best: 0.5733151 (550)	total: 22.2s	remaining: 2.78s
889:	learn: 0.0207023	test: 0.5737734	best: 0.5733151 (550)	total: 22.3s	remaining: 2.75s
890:	learn: 0.0205993	test: 0.5737563	best: 0.5733151 (550)	total: 22.3s	remaining: 2.73s
891:	learn: 0.0205511	test: 0.5737462	best: 0.5733151 (550)	total: 22.3s	remaining: 2.7s
892:	learn: 0.0204978	test: 0.5737496	best: 0.5733151 (550)	total: 22.3s	remaining: 2.67s
893:	learn: 0.0204705	test: 0.5737507	best: 0.5733151 (550)	total: 22.4s	remaining: 2.65s
894:	learn: 0.0204474	test: 0.5737423	best: 0.5733151 (550)	total: 22.4s	remaining: 2.63s
895:	learn: 0.0203806	test: 0.5737147	best: 0.5733151 (550)	total: 22.4s	remaining: 2.6s
896:	learn: 0.0202964	test: 0.5737064	best: 0.5733151 (550)	total: 22.4s	remaining: 2.58s
897:	learn: 0.0202841	test: 0.5737157	best: 0.5733151 (550)	total: 22.4s	remaining: 2.55s
898:	learn: 0

985:	learn: 0.0160164	test: 0.5736829	best: 0.5733151 (550)	total: 24.5s	remaining: 348ms
986:	learn: 0.0160073	test: 0.5736830	best: 0.5733151 (550)	total: 24.5s	remaining: 323ms
987:	learn: 0.0159827	test: 0.5736819	best: 0.5733151 (550)	total: 24.6s	remaining: 298ms
988:	learn: 0.0159228	test: 0.5736635	best: 0.5733151 (550)	total: 24.6s	remaining: 274ms
989:	learn: 0.0159134	test: 0.5736639	best: 0.5733151 (550)	total: 24.6s	remaining: 249ms
990:	learn: 0.0158847	test: 0.5736657	best: 0.5733151 (550)	total: 24.6s	remaining: 224ms
991:	learn: 0.0158742	test: 0.5736619	best: 0.5733151 (550)	total: 24.7s	remaining: 199ms
992:	learn: 0.0158395	test: 0.5736760	best: 0.5733151 (550)	total: 24.7s	remaining: 174ms
993:	learn: 0.0158090	test: 0.5736765	best: 0.5733151 (550)	total: 24.7s	remaining: 149ms
994:	learn: 0.0157505	test: 0.5736920	best: 0.5733151 (550)	total: 24.7s	remaining: 124ms
995:	learn: 0.0157244	test: 0.5736975	best: 0.5733151 (550)	total: 24.8s	remaining: 99.4ms
996:	lear

331:	learn: 0.2477185	test: 0.5058715	best: 0.5057817 (323)
332:	learn: 0.2471218	test: 0.5057925	best: 0.5057817 (323)
333:	learn: 0.2466458	test: 0.5056925	best: 0.5056925 (333)
334:	learn: 0.2462426	test: 0.5056312	best: 0.5056312 (334)
335:	learn: 0.2458812	test: 0.5056504	best: 0.5056312 (334)
336:	learn: 0.2454471	test: 0.5056169	best: 0.5056169 (336)
337:	learn: 0.2450856	test: 0.5054730	best: 0.5054730 (337)
338:	learn: 0.2445370	test: 0.5054037	best: 0.5054037 (338)
339:	learn: 0.2439297	test: 0.5053064	best: 0.5053064 (339)
340:	learn: 0.2434388	test: 0.5051640	best: 0.5051640 (340)
341:	learn: 0.2428566	test: 0.5053020	best: 0.5051640 (340)
342:	learn: 0.2422460	test: 0.5052813	best: 0.5051640 (340)
343:	learn: 0.2417079	test: 0.5052372	best: 0.5051640 (340)
344:	learn: 0.2412951	test: 0.5052068	best: 0.5051640 (340)
345:	learn: 0.2409535	test: 0.5052850	best: 0.5051640 (340)
346:	learn: 0.2404645	test: 0.5054769	best: 0.5051640 (340)
347:	learn: 0.2399427	test: 0.5055169	be

605:	learn: 0.1617788	test: 0.5032573	best: 0.5030883 (588)
606:	learn: 0.1615977	test: 0.5032064	best: 0.5030883 (588)
607:	learn: 0.1611955	test: 0.5031662	best: 0.5030883 (588)
608:	learn: 0.1608638	test: 0.5032968	best: 0.5030883 (588)
609:	learn: 0.1607440	test: 0.5032853	best: 0.5030883 (588)
610:	learn: 0.1605096	test: 0.5032913	best: 0.5030883 (588)
611:	learn: 0.1603320	test: 0.5032934	best: 0.5030883 (588)
612:	learn: 0.1601906	test: 0.5032656	best: 0.5030883 (588)
613:	learn: 0.1599880	test: 0.5032100	best: 0.5030883 (588)
614:	learn: 0.1599024	test: 0.5032146	best: 0.5030883 (588)
615:	learn: 0.1597067	test: 0.5032369	best: 0.5030883 (588)
616:	learn: 0.1596393	test: 0.5032261	best: 0.5030883 (588)
617:	learn: 0.1594811	test: 0.5032407	best: 0.5030883 (588)
618:	learn: 0.1592574	test: 0.5032477	best: 0.5030883 (588)
619:	learn: 0.1590563	test: 0.5032698	best: 0.5030883 (588)
620:	learn: 0.1587513	test: 0.5033309	best: 0.5030883 (588)
621:	learn: 0.1586343	test: 0.5033963	be

899:	learn: 0.1085154	test: 0.5043766	best: 0.5030883 (588)
900:	learn: 0.1083439	test: 0.5044095	best: 0.5030883 (588)
901:	learn: 0.1082171	test: 0.5044166	best: 0.5030883 (588)
902:	learn: 0.1080880	test: 0.5044122	best: 0.5030883 (588)
903:	learn: 0.1079937	test: 0.5044092	best: 0.5030883 (588)
904:	learn: 0.1078153	test: 0.5044279	best: 0.5030883 (588)
905:	learn: 0.1077163	test: 0.5044413	best: 0.5030883 (588)
906:	learn: 0.1076311	test: 0.5044620	best: 0.5030883 (588)
907:	learn: 0.1074412	test: 0.5045038	best: 0.5030883 (588)
908:	learn: 0.1072507	test: 0.5045425	best: 0.5030883 (588)
909:	learn: 0.1071892	test: 0.5045477	best: 0.5030883 (588)
910:	learn: 0.1070024	test: 0.5045537	best: 0.5030883 (588)
911:	learn: 0.1068009	test: 0.5045650	best: 0.5030883 (588)
912:	learn: 0.1067174	test: 0.5045426	best: 0.5030883 (588)
913:	learn: 0.1065647	test: 0.5045499	best: 0.5030883 (588)
914:	learn: 0.1064247	test: 0.5045551	best: 0.5030883 (588)
915:	learn: 0.1063207	test: 0.5045467	be

### Model Training

In [14]:
# training
model.fit(train_pool, eval_set=test_pool, plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 0.1036799	test: 0.0943619	best: 0.0943619 (0)	total: 3.21ms	remaining: 3.21s
1:	learn: 0.1896849	test: 0.1893292	best: 0.1893292 (1)	total: 5.18ms	remaining: 2.59s
2:	learn: 0.2606702	test: 0.2638137	best: 0.2638137 (2)	total: 6.99ms	remaining: 2.32s
3:	learn: 0.3305127	test: 0.3428299	best: 0.3428299 (3)	total: 8.83ms	remaining: 2.2s
4:	learn: 0.3969189	test: 0.4138576	best: 0.4138576 (4)	total: 10.8ms	remaining: 2.15s
5:	learn: 0.4451360	test: 0.4602998	best: 0.4602998 (5)	total: 12.7ms	remaining: 2.1s
6:	learn: 0.4866236	test: 0.5020345	best: 0.5020345 (6)	total: 14.7ms	remaining: 2.09s
7:	learn: 0.5242891	test: 0.5339930	best: 0.5339930 (7)	total: 17.1ms	remaining: 2.12s
8:	learn: 0.5592257	test: 0.5685021	best: 0.5685021 (8)	total: 19.2ms	remaining: 2.12s
9:	learn: 0.5873917	test: 0.5936674	best: 0.5936674 (9)	total: 21.2ms	remaining: 2.1s
10:	learn: 0.6105865	test: 0.6104827	best: 0.6104827 (10)	total: 23.1ms	remaining: 2.08s
11:	learn: 0.6289084	test: 0.6227907	best: 0

142:	learn: 0.9250646	test: 0.7532370	best: 0.7532370 (142)	total: 286ms	remaining: 1.72s
143:	learn: 0.9253636	test: 0.7529507	best: 0.7532370 (142)	total: 288ms	remaining: 1.71s
144:	learn: 0.9259680	test: 0.7523140	best: 0.7532370 (142)	total: 290ms	remaining: 1.71s
145:	learn: 0.9266551	test: 0.7519811	best: 0.7532370 (142)	total: 293ms	remaining: 1.71s
146:	learn: 0.9274855	test: 0.7516406	best: 0.7532370 (142)	total: 296ms	remaining: 1.71s
147:	learn: 0.9283475	test: 0.7513557	best: 0.7532370 (142)	total: 297ms	remaining: 1.71s
148:	learn: 0.9290789	test: 0.7525418	best: 0.7532370 (142)	total: 299ms	remaining: 1.71s
149:	learn: 0.9294715	test: 0.7525220	best: 0.7532370 (142)	total: 303ms	remaining: 1.72s
150:	learn: 0.9303266	test: 0.7522329	best: 0.7532370 (142)	total: 308ms	remaining: 1.73s
151:	learn: 0.9307713	test: 0.7527107	best: 0.7532370 (142)	total: 311ms	remaining: 1.74s
152:	learn: 0.9310092	test: 0.7533327	best: 0.7533327 (152)	total: 313ms	remaining: 1.73s
153:	learn

250:	learn: 0.9633351	test: 0.7584652	best: 0.7585527 (248)	total: 558ms	remaining: 1.66s
251:	learn: 0.9636193	test: 0.7581046	best: 0.7585527 (248)	total: 560ms	remaining: 1.66s
252:	learn: 0.9636782	test: 0.7579250	best: 0.7585527 (248)	total: 563ms	remaining: 1.66s
253:	learn: 0.9638799	test: 0.7578949	best: 0.7585527 (248)	total: 565ms	remaining: 1.66s
254:	learn: 0.9640094	test: 0.7577451	best: 0.7585527 (248)	total: 568ms	remaining: 1.66s
255:	learn: 0.9642634	test: 0.7571073	best: 0.7585527 (248)	total: 575ms	remaining: 1.67s
256:	learn: 0.9645199	test: 0.7575538	best: 0.7585527 (248)	total: 578ms	remaining: 1.67s
257:	learn: 0.9647182	test: 0.7573563	best: 0.7585527 (248)	total: 580ms	remaining: 1.67s
258:	learn: 0.9648579	test: 0.7573465	best: 0.7585527 (248)	total: 582ms	remaining: 1.67s
259:	learn: 0.9650318	test: 0.7567854	best: 0.7585527 (248)	total: 584ms	remaining: 1.66s
260:	learn: 0.9651437	test: 0.7567705	best: 0.7585527 (248)	total: 586ms	remaining: 1.66s
261:	learn

360:	learn: 0.9809367	test: 0.7544890	best: 0.7585527 (248)	total: 844ms	remaining: 1.49s
361:	learn: 0.9810698	test: 0.7546348	best: 0.7585527 (248)	total: 846ms	remaining: 1.49s
362:	learn: 0.9811764	test: 0.7546701	best: 0.7585527 (248)	total: 848ms	remaining: 1.49s
363:	learn: 0.9812972	test: 0.7545913	best: 0.7585527 (248)	total: 850ms	remaining: 1.48s
364:	learn: 0.9814183	test: 0.7548532	best: 0.7585527 (248)	total: 851ms	remaining: 1.48s
365:	learn: 0.9814947	test: 0.7549536	best: 0.7585527 (248)	total: 853ms	remaining: 1.48s
366:	learn: 0.9815897	test: 0.7549678	best: 0.7585527 (248)	total: 855ms	remaining: 1.47s
367:	learn: 0.9816807	test: 0.7547417	best: 0.7585527 (248)	total: 857ms	remaining: 1.47s
368:	learn: 0.9818190	test: 0.7544869	best: 0.7585527 (248)	total: 858ms	remaining: 1.47s
369:	learn: 0.9819461	test: 0.7545386	best: 0.7585527 (248)	total: 860ms	remaining: 1.46s
370:	learn: 0.9819827	test: 0.7545531	best: 0.7585527 (248)	total: 862ms	remaining: 1.46s
371:	learn

515:	learn: 0.9909421	test: 0.7537633	best: 0.7585527 (248)	total: 1.12s	remaining: 1.05s
516:	learn: 0.9909766	test: 0.7536875	best: 0.7585527 (248)	total: 1.12s	remaining: 1.05s
517:	learn: 0.9909972	test: 0.7536612	best: 0.7585527 (248)	total: 1.13s	remaining: 1.05s
518:	learn: 0.9910136	test: 0.7535989	best: 0.7585527 (248)	total: 1.13s	remaining: 1.05s
519:	learn: 0.9910630	test: 0.7534878	best: 0.7585527 (248)	total: 1.13s	remaining: 1.04s
520:	learn: 0.9911684	test: 0.7533815	best: 0.7585527 (248)	total: 1.13s	remaining: 1.04s
521:	learn: 0.9911853	test: 0.7533855	best: 0.7585527 (248)	total: 1.13s	remaining: 1.04s
522:	learn: 0.9912502	test: 0.7534724	best: 0.7585527 (248)	total: 1.14s	remaining: 1.04s
523:	learn: 0.9912889	test: 0.7535306	best: 0.7585527 (248)	total: 1.14s	remaining: 1.03s
524:	learn: 0.9913325	test: 0.7536060	best: 0.7585527 (248)	total: 1.14s	remaining: 1.03s
525:	learn: 0.9913861	test: 0.7536428	best: 0.7585527 (248)	total: 1.14s	remaining: 1.03s
526:	learn

656:	learn: 0.9948499	test: 0.7522983	best: 0.7585527 (248)	total: 1.4s	remaining: 733ms
657:	learn: 0.9948605	test: 0.7521251	best: 0.7585527 (248)	total: 1.41s	remaining: 731ms
658:	learn: 0.9948772	test: 0.7521005	best: 0.7585527 (248)	total: 1.41s	remaining: 729ms
659:	learn: 0.9948928	test: 0.7520437	best: 0.7585527 (248)	total: 1.41s	remaining: 727ms
660:	learn: 0.9949172	test: 0.7520726	best: 0.7585527 (248)	total: 1.41s	remaining: 725ms
661:	learn: 0.9949452	test: 0.7519865	best: 0.7585527 (248)	total: 1.41s	remaining: 722ms
662:	learn: 0.9949630	test: 0.7520187	best: 0.7585527 (248)	total: 1.42s	remaining: 720ms
663:	learn: 0.9949916	test: 0.7520663	best: 0.7585527 (248)	total: 1.42s	remaining: 718ms
664:	learn: 0.9950103	test: 0.7520973	best: 0.7585527 (248)	total: 1.42s	remaining: 716ms
665:	learn: 0.9950122	test: 0.7520773	best: 0.7585527 (248)	total: 1.42s	remaining: 714ms
666:	learn: 0.9950361	test: 0.7519277	best: 0.7585527 (248)	total: 1.43s	remaining: 712ms
667:	learn:

766:	learn: 0.9966739	test: 0.7512545	best: 0.7585527 (248)	total: 1.68s	remaining: 511ms
767:	learn: 0.9966815	test: 0.7513148	best: 0.7585527 (248)	total: 1.68s	remaining: 508ms
768:	learn: 0.9966998	test: 0.7513203	best: 0.7585527 (248)	total: 1.68s	remaining: 506ms
769:	learn: 0.9967127	test: 0.7514448	best: 0.7585527 (248)	total: 1.69s	remaining: 504ms
770:	learn: 0.9967315	test: 0.7513951	best: 0.7585527 (248)	total: 1.69s	remaining: 501ms
771:	learn: 0.9967539	test: 0.7514171	best: 0.7585527 (248)	total: 1.69s	remaining: 499ms
772:	learn: 0.9967703	test: 0.7512955	best: 0.7585527 (248)	total: 1.69s	remaining: 497ms
773:	learn: 0.9967916	test: 0.7513343	best: 0.7585527 (248)	total: 1.69s	remaining: 494ms
774:	learn: 0.9968072	test: 0.7515074	best: 0.7585527 (248)	total: 1.7s	remaining: 492ms
775:	learn: 0.9968230	test: 0.7515003	best: 0.7585527 (248)	total: 1.7s	remaining: 490ms
776:	learn: 0.9968413	test: 0.7513591	best: 0.7585527 (248)	total: 1.7s	remaining: 488ms
777:	learn: 0

922:	learn: 0.9981893	test: 0.7511136	best: 0.7585527 (248)	total: 1.96s	remaining: 164ms
923:	learn: 0.9982017	test: 0.7511786	best: 0.7585527 (248)	total: 1.96s	remaining: 161ms
924:	learn: 0.9982025	test: 0.7511105	best: 0.7585527 (248)	total: 1.96s	remaining: 159ms
925:	learn: 0.9982128	test: 0.7510094	best: 0.7585527 (248)	total: 1.97s	remaining: 157ms
926:	learn: 0.9982232	test: 0.7510600	best: 0.7585527 (248)	total: 1.97s	remaining: 155ms
927:	learn: 0.9982346	test: 0.7510926	best: 0.7585527 (248)	total: 1.97s	remaining: 153ms
928:	learn: 0.9982409	test: 0.7510836	best: 0.7585527 (248)	total: 1.97s	remaining: 151ms
929:	learn: 0.9982508	test: 0.7510772	best: 0.7585527 (248)	total: 1.97s	remaining: 148ms
930:	learn: 0.9982568	test: 0.7510456	best: 0.7585527 (248)	total: 1.97s	remaining: 146ms
931:	learn: 0.9982574	test: 0.7510394	best: 0.7585527 (248)	total: 1.98s	remaining: 144ms
932:	learn: 0.9982577	test: 0.7510387	best: 0.7585527 (248)	total: 1.98s	remaining: 142ms
933:	learn

### Model Prediction

In [15]:
# prediction
preds = model.predict(test_pool)

In [17]:
print(preds)

[ 1.37517996e-01  1.66898778e+00  7.57846506e-03 -1.23834379e-01
  7.40000839e-02  2.34503955e-01  6.37640674e-01  2.02563100e+00
  1.94310911e-01  1.57112462e-01  2.33201984e-01  1.63089253e+00
  6.04258870e-03  1.50978434e-02  7.74394192e-01 -7.37500217e-02
  3.72058454e-01  1.04382157e+00 -1.30564201e-02  1.61013113e-01
  1.21437954e-01  4.34100649e-02  2.89711438e-01  1.72882314e-01
  1.73629539e+00 -9.15874704e-02  1.46632095e-01  1.55047697e-01
  5.97548611e-01  2.05044561e-02 -4.83250995e-02  2.49352107e-01
  3.64203709e-02  2.19514675e-01 -7.01137613e-02  2.08082995e-01
  1.89414358e-01  1.13746955e-01  2.91153457e-02  6.90917620e-02
 -3.42597457e-02 -3.72554527e-02  1.86951165e+00  3.54717744e-01
 -1.79945646e-02  6.58370893e-01  2.28011181e-01  9.36692871e-02
  1.23017231e+00  4.68665065e-01  2.49911750e-01  1.07071967e-01
  1.35880017e+00 -7.37456529e-02  6.47858245e-03  6.75493368e-02
  1.69560780e+00  1.80664059e+00  1.94014996e+00  5.19638015e-01
  1.63686317e+00 -6.84872

### Saving the Model 

In [16]:
# model.save_model("catboost")